In [1]:
import pandas as pd 
import os 
import altair as alt 

In [2]:
os.getcwd()

'e:\\StudyTime\\Fall\\Data Viz\\statewise-economy\\code'

In [3]:
state_data = pd.read_csv('../data/data_2024_cleaned.csv')
state_data.head()

GeoFips          GeoName  LineCode  \
0        0  United States *         1   
1        0  United States *         2   
2        0  United States *         3   
3        0  United States *         6   
4        0  United States *        10   

                                         Description        2023  Unnamed: 5  
0                                 All industry total  27811517.0       27.81  
1                                 Private industries  24712793.0       24.71  
2         Agriculture, forestry, fishing and hunting    270441.0        0.27  
3      Mining, quarrying, and oil and gas extraction    411819.0        0.41  
4                                          Utilities    457772.0        0.46

In [4]:
state_data.columns


Index(['GeoFips', 'GeoName', 'LineCode', 'Description', '2023', 'Unnamed: 5'], dtype='object')

In [5]:
filtered_data = state_data[state_data['Industry'] == 'Agriculture, forestry, fishing and hunting']

KeyError: 'Industry'

In [6]:
filtered_data.head()

NameError: name 'filtered_data' is not defined

In [7]:
bar_chart = alt.Chart(filtered_data).mark_bar().encode(
    x=alt.X('States:N', sort='-y'),
    y='Total in USD Trillions:Q'
)

bar_chart.show()

NameError: name 'filtered_data' is not defined

In [ ]:
state_data['Industry'].unique()

array(['All industry total', 'Private industries',
       'Agriculture, forestry, fishing and hunting',
       'Mining, quarrying, and oil and gas extraction', 'Utilities',
       'Construction', 'Manufacturing', 'Wholesale trade', 'Retail trade',
       'Transportation and warehousing', 'Information',
       'Finance and insurance', 'Real estate and rental and leasing',
       'Professional, scientific, and technical services',
       'Management of companies and enterprises',
       'Administrative and support and waste management and remediation services',
       'Educational services', 'Health care and social assistance',
       'Arts, entertainment, and recreation',
       'Accommodation and food services',
       'Other services (except government and government enterprises)',
       'Government and government enterprises'], dtype=object)

In [8]:
state_data['Industry'].unique()


KeyError: 'Industry'

In [9]:
state_data_noUS = state_data[state_data['States'] != 'United States *']
state_data2 = state_data_noUS[~state_data_noUS['Industry'].isin(['All industry total', 'Private industries'])]


KeyError: 'States'

In [10]:
industry_list = list(state_data_noUS['Industry'].unique())

industry_dropdown = alt.binding_select(
    options=industry_list,
    name='Select Industry: '
)

industry_select = alt.selection_point(
    fields=['Industry'],
    bind=industry_dropdown,
    value=industry_list[0]
)

chart = (
    alt.Chart(state_data_noUS)
    .mark_bar()
    .encode(
        x=alt.X('States:N', sort='-y'),
        y='Total in USD Trillions:Q'
    )
    .add_selection(industry_select)
    .transform_filter(industry_select)
)

chart.show()


NameError: name 'state_data_noUS' is not defined

In [11]:
state_list = list(state_data_noUS['States'].unique())

state_dropdown = alt.binding_select(
    options=state_list,
    name='Select State: '
)

state_select = alt.selection_point(
    fields=['States'],
    bind=state_dropdown,
    value=state_list[0]
)

chart = (
    alt.Chart(state_data2)
    .mark_bar()
    .encode(
        x=alt.X('Industry:N', sort='-y'),
        y='Total in USD Trillions:Q'
    )
    .add_selection(state_select)
    .transform_filter(state_select)
)

chart.show()


NameError: name 'state_data_noUS' is not defined

In [12]:
state_data['States'].unique()


KeyError: 'States'

In [ ]:
df2024 = pd.read_excel("../data/data_file.xlsx", sheet_name="2024")
df2023 = pd.read_excel("../data/data_file.xlsx", sheet_name="2023")


In [15]:
import altair as alt
alt.data_transformers.disable_max_rows()

DataTransformerRegistry.enable('default')

In [16]:
import pandas as pd
import altair as alt

# --------------------------------------------------------
# 1. LOAD EXCEL SHEETS & COMBINE
# --------------------------------------------------------

# Load the two sheets from your Excel file
df2019 = pd.read_excel("../data/data_file.xlsx", sheet_name="2019")
df2020 = pd.read_excel("../data/data_file.xlsx", sheet_name="2020")
df2021 = pd.read_excel("../data/data_file.xlsx", sheet_name="2021")
df2022 = pd.read_excel("../data/data_file.xlsx", sheet_name="2022")
df2023 = pd.read_excel("../data/data_file.xlsx", sheet_name="2023")
df2024 = pd.read_excel("../data/data_file.xlsx", sheet_name="2024")


# Add Year column
df2019["Year"] = 2019
df2020["Year"] = 2020
df2021["Year"] = 2021
df2022["Year"] = 2022
df2023["Year"] = 2023
df2024["Year"] = 2024


# Combine into one dataframe
state_data_all = pd.concat([df2019, df2020, df2021, df2022, df2023, df2024], ignore_index=True)

# Clean whitespace if any exists
state_data_all["States"] = state_data_all["States"].str.strip()
state_data_all["Industry"] = state_data_all["Industry"].str.strip()
state_data_all = state_data_all[state_data_all["States"] != "United States *"]

# --------------------------------------------------------
# 2. CREATE DROPDOWNS
# --------------------------------------------------------

# Industry dropdown
industry_list = sorted(state_data_all["Industry"].unique().tolist())

industry_dropdown = alt.binding_select(
    options=industry_list,
    name="Select Industry: "
)

industry_select = alt.selection_point(
    fields=["Industry"],
    bind=industry_dropdown,
    value=industry_list[0]       # default industry
)

# Year dropdown
years = sorted(state_data_all["Year"].unique().tolist())

year_dropdown = alt.binding_select(
    options=years,
    name="Select Year: "
)

year_select = alt.selection_point(
    fields=["Year"],
    bind=year_dropdown,
    value=years[0]               # default year
)


# --------------------------------------------------------
# 3. BUILD THE INDUSTRY × YEAR FILTERED CHART
# --------------------------------------------------------

chart = (
    alt.Chart(state_data_all)
    .mark_bar()
    .encode(
        x=alt.X("States:N", sort="-y", title="States"),
        y=alt.Y("Total in USD Trillions:Q", title="Earnings"),
        tooltip=["States", "Industry", "Total in USD Trillions", "Year"]
    )
    .add_selection(industry_select, year_select)
    .transform_filter(industry_select)
    .transform_filter(year_select)
    .properties(
        width=750,
        height=450,
        title="State-wise Comparison by Industry and Year"
    )
)

chart


C:\Users\Shumaila Abbasi\AppData\Local\Temp\ipykernel_10912\460766031.py:79: AltairDeprecationWarning: 
Deprecated since `altair=5.0.0`. Use add_params instead.
  .add_selection(industry_select, year_select)


alt.Chart(...)

In [17]:
state_data_all.columns = state_data_all.columns.str.strip()


In [19]:
state_data_all.columns


Index(['GeoFips', 'States', 'LineCode', 'Industry', 'Total',
       'Total in USD Trillions', 'Year'],
      dtype='object')

In [20]:
import pandas as pd
import altair as alt

# --------------------------------------------------------
# 1. LOAD YOUR EXCEL FILE
# --------------------------------------------------------

df = pd.read_excel("../data/new_data_file.xlsx")

# Clean whitespace in column names
df.columns = df.columns.astype(str).str.strip()

# Fix Total column if needed
df = df.rename(columns={"Total ": "Total"})

print("Columns:", df.columns.tolist())

# --------------------------------------------------------
# 2. IDENTIFY YEAR COLUMNS (2019–2024)
# --------------------------------------------------------

year_cols = [col for col in df.columns if col.isdigit()]
print("Detected year columns:", year_cols)

# --------------------------------------------------------
# 3. MELT WIDE → LONG FORMAT
# --------------------------------------------------------

state_data_all = pd.melt(
    df,
    id_vars=["GeoFips", "States", "LineCode", "Industry", "Total"],
    value_vars=year_cols,
    var_name="Year",
    value_name="Total in USD Trillions"
)

# --------------------------------------------------------
# 4. CLEAN MELTED DATA
# --------------------------------------------------------

state_data_all["States"] = state_data_all["States"].astype(str).str.strip()
state_data_all["Industry"] = state_data_all["Industry"].astype(str).str.strip()
state_data_all["Year"] = state_data_all["Year"].astype(int)

# Remove national totals
state_data_all = state_data_all[state_data_all["States"] != "United States"]


# --------------------------------------------------------
# 5. DROPDOWNS
# --------------------------------------------------------

industry_list = sorted(state_data_all["Industry"].unique().tolist())
year_list = sorted(state_data_all["Year"].unique().tolist())

industry_dropdown = alt.binding_select(
    options=industry_list,
    name="Select Industry: "
)

year_dropdown = alt.binding_select(
    options=year_list,
    name="Select Year: "
)

industry_select = alt.selection_point(
    fields=["Industry"],
    bind=industry_dropdown,
    value=industry_list[0]   # default first industry
)

year_select = alt.selection_point(
    fields=["Year"],
    bind=year_dropdown,
    value=year_list[0]
)

# --------------------------------------------------------
# 6. CUSTOM COLOR PALETTE FOR INDUSTRIES
# --------------------------------------------------------

industry_colors = {
    "Agriculture, forestry, fishing and hunting": "#1f77b4",
    "Mining, quarrying, and oil and gas extraction": "#ff7f0e",
    "Utilities": "#2ca02c",
    "Construction": "#d62728",
    "Manufacturing": "#9467bd",
    "Wholesale trade": "#8c564b",
    "Retail trade": "#e377c2",
    "Transportation and warehousing": "#7f7f7f",
    "Information": "#bcbd22",
    "Finance and insurance": "#17becf",
    "Real estate and rental and leasing": "#aec7e8",
    "Professional, scientific, and technical services": "#ffbb78",
    "Management of companies and enterprises": "#98df8a",
    "Administrative and support and waste management and remediation services": "#ff9896",
    "Educational services": "#c5b0d5",
    "Health care and social assistance": "#c49c94",
    "Arts, entertainment, and recreation": "#f7b6d2",
    "Accommodation and food services": "#dbdb8d",
    "Other services (except government and government enterprises)": "#9edae5",
    "Government and government enterprises": "#ad494a"
}

# --------------------------------------------------------
# 7. FINAL INTERACTIVE BAR CHART
# --------------------------------------------------------

chart = (
    alt.Chart(state_data_all)
    .mark_bar()
    .encode(
        x=alt.X("States:N", sort="-y", title="States"),
        y=alt.Y("Total in USD Trillions:Q", title="Earnings (USD Trillions)"),

        # Apply unique color to each industry (even when filtered to 1)
        color=alt.Color(
            "Industry:N",
            scale=alt.Scale(
                domain=list(industry_colors.keys()),
                range=list(industry_colors.values())
            ),
            legend=None
        ),

        tooltip=["States", "Industry", "Year", "Total in USD Trillions"]
    )
    .add_selection(industry_select, year_select)
    .transform_filter(industry_select)
    .transform_filter(year_select)
    .properties(
        width=900,
        height=480,
        title="State-wise Earnings Comparison by Industry and Year"
    )
)

chart


Columns: ['GeoFips', 'States', 'LineCode', 'Industry', 'Total', '2019', '2020', '2021', '2022', '2023', '2024']
Detected year columns: ['2019', '2020', '2021', '2022', '2023', '2024']


C:\Users\Shumaila Abbasi\AppData\Local\Temp\ipykernel_10912\2390801250.py:128: AltairDeprecationWarning: 
Deprecated since `altair=5.0.0`. Use add_params instead.
  .add_selection(industry_select, year_select)


alt.Chart(...)

In [21]:
df = pd.read_excel("../data/new_data_file.xlsx")   
df.columns


Index([ 'GeoFips',   'States', 'LineCode', 'Industry',   'Total ',       2019,
             2020,       2021,       2022,       2023,       2024],
      dtype='object')

In [22]:
import pandas as pd
import altair as alt

# --------------------------------------------------------
# 1. LOAD EXCEL FILE
# --------------------------------------------------------

df = pd.read_excel("../data/industry_wise.xlsx")

# Clean column names
df.columns = df.columns.astype(str).str.strip()

# Identify year columns (numeric)
year_cols = [col for col in df.columns if col.isdigit()]

# Remove commas from numeric cells
for col in year_cols:
    df[col] = df[col].astype(str).str.replace(",", "")
    df[col] = pd.to_numeric(df[col], errors="coerce")

# --------------------------------------------------------
# 2. MELT WIDE → LONG FORMAT
# --------------------------------------------------------

state_data_all = pd.melt(
    df,
    id_vars=["GeoFips", "States", "LineCode", "Industry"],
    value_vars=year_cols,
    var_name="Year",
    value_name="Total in USD Billions"
)

# --------------------------------------------------------
# 3. CLEAN DATA
# --------------------------------------------------------

state_data_all["States"] = state_data_all["States"].astype(str).str.strip()
state_data_all["Industry"] = state_data_all["Industry"].astype(str).str.strip()
state_data_all["Year"] = state_data_all["Year"].astype(int)

# Remove national total rows
bad_labels = ["United States *", "United States", "United States*"]
state_data_all = state_data_all[~state_data_all["States"].isin(bad_labels)]

# --------------------------------------------------------
# 4. DROPDOWNS
# --------------------------------------------------------

state_list = sorted(state_data_all["States"].unique().tolist())
year_list = sorted(state_data_all["Year"].unique().tolist())

state_dropdown = alt.binding_select(options=state_list, name="Select State: ")
year_dropdown = alt.binding_select(options=year_list, name="Select Year: ")

state_select = alt.selection_point(fields=["States"], bind=state_dropdown, value=state_list[0])
year_select = alt.selection_point(fields=["Year"], bind=year_dropdown, value=year_list[0])

# --------------------------------------------------------
# 5. INDUSTRY COLORS
# --------------------------------------------------------

industry_colors = {
    "Agriculture, forestry, fishing and hunting": "#1f77b4",
    "Mining, quarrying, and oil and gas extraction": "#ff7f0e",
    "Utilities": "#2ca02c",
    "Construction": "#d62728",
    "Manufacturing": "#9467bd",
    "Wholesale trade": "#8c564b",
    "Retail trade": "#e377c2",
    "Transportation and warehousing": "#7f7f7f",
    "Information": "#bcbd22",
    "Finance and insurance": "#17becf",
    "Real estate and rental and leasing": "#aec7e8",
    "Professional, scientific, and technical services": "#ffbb78",
    "Management of companies and enterprises": "#98df8a",
    "Administrative and support and waste management and remediation services": "#ff9896",
    "Educational services": "#c5b0d5",
    "Health care and social assistance": "#c49c94",
    "Arts, entertainment, and recreation": "#f7b6d2",
    "Accommodation and food services": "#dbdb8d",
    "Other services (except government and government enterprises)": "#9edae5",
    "Government and government enterprises": "#ad494a",
    "All industry total": "#6baed6",
    "Private industries": "#9ecae1"
}

# --------------------------------------------------------
# 6. FINAL CHART (WITH LABEL FIX)
# --------------------------------------------------------

chart = (
    alt.Chart(state_data_all)
    .mark_bar()
    .encode(
        x=alt.X(
            "Industry:N",
            sort="-y",
            title="Industry",
            axis=alt.Axis(labelAngle=-40, labelLimit=300)
        ),
        y=alt.Y("Total in USD Billions:Q", title="Earnings (Billions USD)"),
        color=alt.Color(
            "Industry:N",
            scale=alt.Scale(
                domain=list(industry_colors.keys()),
                range=list(industry_colors.values())
            ),
            legend=None
        ),
        tooltip=["States", "Industry", "Year", "Total in USD Billions"]
    )
    .add_selection(state_select, year_select)
    .transform_filter(state_select)
    .transform_filter(year_select)
    .properties(
        width=1300,
        height=500,
        title="Industry Earnings for Selected State and Year"
    )
)

chart


C:\Users\Shumaila Abbasi\AppData\Local\Temp\ipykernel_10912\2138175375.py:112: AltairDeprecationWarning: 
Deprecated since `altair=5.0.0`. Use add_params instead.
  .add_selection(state_select, year_select)


alt.Chart(...)

In [ ]:
import pandas as pd
import altair as alt

# --------------------------------------------------------
# 1. LOAD DATA
# --------------------------------------------------------

df = pd.read_excel("../data/trend.xlsx")

# Clean column names
df.columns = df.columns.astype(str).str.strip()

# Identify growth columns (have %)
growth_cols = [col for col in df.columns if "-" in col]

# Remove '%' and convert to decimal
for col in growth_cols:
    df[col] = df[col].astype(str).str.replace("%", "").str.replace(",", "")
    df[col] = pd.to_numeric(df[col], errors="coerce") / 100.0

# --------------------------------------------------------
# 2. MELT WIDE → LONG
# --------------------------------------------------------

df_long = pd.melt(
    df,
    id_vars=["GeoFips", "States", "LineCode", "Industry"],
    value_vars=growth_cols,
    var_name="Period",
    value_name="GrowthRate"
)

# Clean text columns
df_long["States"] = df_long["States"].astype(str).str.strip()
df_long["Industry"] = df_long["Industry"].astype(str).str.strip()

# Remove national totals
bad = ["United States", "United States*", "United States *"]
df_long = df_long[~df_long["States"].isin(bad)]

# --------------------------------------------------------
# 3. DROPDOWNS
# --------------------------------------------------------

state_list = sorted(df_long["States"].unique().tolist())
industry_list = sorted(df_long["Industry"].unique().tolist())

state_dropdown = alt.binding_select(options=state_list, name="Select State: ")
industry_dropdown = alt.binding_select(options=industry_list, name="Select Industry: ")

state_select = alt.selection_point(fields=["States"], bind=state_dropdown, value=state_list[0])
industry_select = alt.selection_point(fields=["Industry"], bind=industry_dropdown, value=industry_list[0])

# --------------------------------------------------------
# 4. LINE CHART — GROWTH RATE OVER TIME
# --------------------------------------------------------

chart = (
    alt.Chart(df_long)
    .mark_line(point=True, strokeWidth=3)
    .encode(
        x=alt.X("Period:N", sort=growth_cols, title="Yearly Change"),
        y=alt.Y("GrowthRate:Q", title="Growth Rate", axis=alt.Axis(format="%", labelOverlap=True)),
        tooltip=["States", "Industry", "Period", alt.Tooltip("GrowthRate:Q", format=".1%")],
        color=alt.value("#1f77b4")
    )
    .add_selection(state_select, industry_select)
    .transform_filter(state_select)
    .transform_filter(industry_select)
    .properties(
        width=700,
        height=400,
        title="Growth Trend for Selected State and Industry"
    )
)

chart


C:\Users\Shumaila Abbasi\AppData\Local\Temp\ipykernel_21272\2710137513.py:67: AltairDeprecationWarning: 
Deprecated since `altair=5.0.0`. Use add_params instead.
  .add_selection(state_select, industry_select)


alt.Chart(...)

In [23]:
import pandas as pd
import altair as alt

# --------------------------------------------------------
# 1. LOAD DATA
# --------------------------------------------------------

df = pd.read_excel("../data/new_data_file.xlsx")

# Clean column names
df.columns = df.columns.astype(str).str.strip()

# Identify actual year columns
year_cols = ["2019", "2020", "2021", "2022", "2023", "2024"]

# Convert year columns to numeric
for col in year_cols:
    df[col] = (
        df[col]
        .astype(str)
        .str.replace(",", "")
    )
    df[col] = pd.to_numeric(df[col], errors="coerce")

# --------------------------------------------------------
# 2. CREATE GROWTH COLUMNS AUTOMATICALLY
# --------------------------------------------------------

growth_map = {
    "2019-20": ("2019", "2020"),
    "2020-21": ("2020", "2021"),
    "2021-22": ("2021", "2022"),
    "2022-23": ("2022", "2023"),
    "2023-24": ("2023", "2024"),
}

for new_col, (prev_year, next_year) in growth_map.items():
    df[new_col] = (df[next_year] - df[prev_year]) / df[prev_year]

growth_cols = list(growth_map.keys())

# --------------------------------------------------------
# 3. MELT WIDE → LONG FORMAT
# --------------------------------------------------------

df_long = pd.melt(
    df,
    id_vars=["GeoFips", "States", "LineCode", "Industry"],
    value_vars=growth_cols,
    var_name="Period",
    value_name="GrowthRate"
)

# --------------------------------------------------------
# 4. CLEAN DATA
# --------------------------------------------------------

df_long["States"] = df_long["States"].astype(str).str.strip()
df_long["Industry"] = df_long["Industry"].astype(str).str.strip()

bad = ["United States", "United States*", "United States *"]
df_long = df_long[~df_long["States"].isin(bad)]

# --------------------------------------------------------
# 5. DROPDOWNS
# --------------------------------------------------------

state_list = sorted(df_long["States"].unique().tolist())
industry_list = sorted(df_long["Industry"].unique().tolist())

state_dropdown = alt.binding_select(options=state_list, name="Select State: ")
industry_dropdown = alt.binding_select(options=industry_list, name="Select Industry: ")

state_select = alt.selection_point(fields=["States"], bind=state_dropdown, value=state_list[0])
industry_select = alt.selection_point(fields=["Industry"], bind=industry_dropdown, value=industry_list[0])

# --------------------------------------------------------
# 6. INDUSTRY COLOR PALETTE
# --------------------------------------------------------

industry_colors = {
    "Agriculture, forestry, fishing and hunting": "#1f77b4",
    "Mining, quarrying, and oil and gas extraction": "#ff7f0e",
    "Utilities": "#2ca02c",
    "Construction": "#d62728",
    "Manufacturing": "#9467bd",
    "Wholesale trade": "#8c564b",
    "Retail trade": "#e377c2",
    "Transportation and warehousing": "#7f7f7f",
    "Information": "#bcbd22",
    "Finance and insurance": "#17becf",
    "Real estate and rental and leasing": "#aec7e8",
    "Professional, scientific, and technical services": "#ffbb78",
    "Management of companies and enterprises": "#98df8a",
    "Administrative and support and waste management and remediation services": "#ff9896",
    "Educational services": "#c5b0d5",
    "Health care and social assistance": "#c49c94",
    "Arts, entertainment, and recreation": "#f7b6d2",
    "Accommodation and food services": "#dbdb8d",
    "Other services (except government and government enterprises)": "#9edae5",
    "Government and government enterprises": "#ad494a",
    "All industry total": "#6baed6",
    "Private industries": "#9ecae1"
}

# --------------------------------------------------------
# 7. FINAL TREND CHART (OPTION C)
# --------------------------------------------------------

chart = (
    alt.Chart(df_long)
    .mark_line(point=True, strokeWidth=3)
    .encode(
        x=alt.X("Period:N", sort=growth_cols, title="Yearly Growth Period"),
        y=alt.Y("GrowthRate:Q", title="Growth Rate", axis=alt.Axis(format="%", labelOverlap=True)),
        color=alt.Color(
            "Industry:N",
            scale=alt.Scale(
                domain=list(industry_colors.keys()),
                range=list(industry_colors.values())
            ),
            legend=None
        ),
        tooltip=[
            "States",
            "Industry",
            "Period",
            alt.Tooltip("GrowthRate:Q", format=".1%")
        ]
    )
    .add_selection(state_select, industry_select)
    .transform_filter(state_select)
    .transform_filter(industry_select)
    .properties(
        width=700,
        height=400,
        title="Growth Trend for Selected State & Industry (2019–24)"
    )
)

chart


C:\Users\Shumaila Abbasi\AppData\Local\Temp\ipykernel_10912\1993799553.py:131: AltairDeprecationWarning: 
Deprecated since `altair=5.0.0`. Use add_params instead.
  .add_selection(state_select, industry_select)


alt.Chart(...)